In [165]:
import pandas as pd 
import numpy as np
from lightgbm import LGBMClassifier
from sklearn.metrics import f1_score
from sklearn.metrics import roc_auc_score
from sklearn.metrics import  accuracy_score
from sklearn.linear_model import LogisticRegression


In [166]:
train  = pd.read_csv('train.csv')
test  = pd.read_csv('test.csv')

In [167]:
train.fillna(0, inplace=True)
test.fillna(0, inplace=True)

In [168]:
for df in train,test:
    df.drop(columns='Unnamed: 0',inplace=True,errors='ignore')

In [169]:
features = []
with open('adhd_features.txt') as f:
    for line in f:
        features.append(line.strip())

In [170]:
target = 'Sex_F'

In [171]:
participant_id = train['participant_id']
sex = train[target]
adhd = train['ADHD_Outcome']
train = train[features]

train['participant_id'] = participant_id
train[target] = sex

In [172]:
test_participant_id = test['participant_id']
test = test[features]
test['participant_id'] = test_participant_id

/tmp/ipykernel_6003/3949435736.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test['participant_id'] = test_participant_id


In [173]:
# knn_i = KNNImputer(n_neighbors=5, weights='uniform')
# train[features] = knn_i.fit_transform(train[features])
# test[features] = knn_i.fit_transform(test[features])

In [174]:
train

Basic_Demos_Enroll_Year  Barratt_Barratt_P1_Occ  \
0                        2019                    45.0   
1                        2017                     0.0   
2                        2017                     0.0   
3                        2018                    10.0   
4                        2018                     0.0   
...                       ...                     ...   
1208                     2019                     0.0   
1209                     2018                    40.0   
1210                     2018                    40.0   
1211                     2019                    35.0   
1212                     2017                    35.0   

      SDQ_SDQ_Difficulties_Total  SDQ_SDQ_Externalizing  \
0                           17.0                   11.0   
1                           20.0                   13.0   
2                           24.0                   10.0   
3                            5.0                    3.0   
4                           23.0                   15.0   
...                          ...                    ...   
1208                        20.0                   13.0   
1209                         5.0                    5.0   
1210                        14.0                    9.0   
1211                        10.0                    8.0   
1212                        11.0                    9.0   

      SDQ_SDQ_Generating_Impact  SDQ_SDQ_Hyperactivity  0throw_10thcolumn  \
0                           5.0                    8.0           0.049068   
1                           5.0                    8.0           0.181864   
2                          10.0                    7.0           0.519783   
3                           0.0                    3.0          -0.004607   
4                           8.0                    9.0           0.226854   
...                         ...                    ...                ...   
1208                        5.0                    8.0           0.039043   
1209                        0.0                    3.0           0.219034   
1210                        3.0                    7.0          -0.203159   
1211                        5.0                    7.0           0.617983   
1212                        4.0                    7.0           0.147600   

      0throw_17thcolumn  0throw_21thcolumn  0throw_46thcolumn  ...  \
0             -0.140341          -0.224897          -0.412569  ...   
1             -0.105757          -0.033084          -0.364414  ...   
2              0.176966          -0.209339          -0.132239  ...   
3             -0.100754          -0.044241          -0.122701  ...   
4             -0.295974          -0.092363          -0.124803  ...   
...                 ...                ...                ...  ...   
1208          -0.164408           0.131465          -0.101193  ...   
1209          -0.058831           0.257789           0.291480  ...   
1210          -0.285079          -0.247803          -0.399821  ...   
1211           0.026933          -0.273390          -0.028228  ...   
1212           0.063227          -0.407332          -0.218204  ...   

      184throw_189thcolumn  184throw_193thcolumn  184throw_199thcolumn  \
0                 0.728053              0.540650              0.140921   
1                 0.345310              0.197567              0.096753   
2                 0.392205              0.509720             -0.387180   
3                 0.082132              0.308109              0.069957   
4                 0.394607              0.332700             -0.179066   
...                    ...                   ...                   ...   
1208              0.443414              0.278748             -0.540079   
1209              0.000325             -0.164930              0.070914   
1210              0.103732              0.010662             -0.049496   
1211              0.331160              0.123954             -0.021683   
1212              0.061583      

In [175]:
test

Basic_Demos_Enroll_Year  Barratt_Barratt_P1_Occ  \
0                       2022                    30.0   
1                       2023                    45.0   
2                       2022                    40.0   
3                       2022                    45.0   
4                       2022                     0.0   
..                       ...                     ...   
299                     2023                     0.0   
300                     2023                    35.0   
301                     2023                    25.0   
302                     2022                     0.0   
303                     2022                     0.0   

     SDQ_SDQ_Difficulties_Total  SDQ_SDQ_Externalizing  \
0                          12.0                    9.0   
1                          16.0                    5.0   
2                           7.0                    6.0   
3                          15.0                   10.0   
4                          18.0                   12.0   
..                          ...                    ...   
299                        18.0                    7.0   
300                        16.0                   11.0   
301                        11.0                    4.0   
302                        21.0                   10.0   
303                         4.0                    4.0   

     SDQ_SDQ_Generating_Impact  SDQ_SDQ_Hyperactivity  0throw_10thcolumn  \
0                          2.0                    7.0           0.470220   
1                          7.0                    3.0           0.275052   
2                          1.0                    5.0           0.301871   
3                          8.0                    6.0           0.417308   
4                          5.0                   10.0           0.304429   
..                         ...                    ...                ...   
299                        5.0                    6.0           0.265432   
300                        5.0                    9.0           0.049262   
301                        4.0                    3.0           0.371101   
302                        6.0                    5.0           0.172004   
303                        3.0                    4.0           0.488218   

     0throw_17thcolumn  0throw_21thcolumn  0throw_46thcolumn  ...  \
0            -0.080816          -0.223550          -0.309777  ...   
1             0.129341          -0.341092          -0.303224  ...   
2             0.075495           0.065360           0.068137  ...   
3            -0.148932           0.007070          -0.001910  ...   
4            -0.309398          -0.164119          -0.204350  ...   
..                 ...                ...                ...  ...   
299          -0.315226           0.007329          -0.069768  ...   
300          -0.090644          -0.220063          -0.278171  ...   
301          -0.144907          -0.139323          -0.169582  ...   
302          -0.103170          -0.293404          -0.077136  ...   
303           0.253668           0.247507          -0.179780  ...   

     184throw_187thcolumn  184throw_189thcolumn  184throw_193thcolumn  \
0                0.251256              0.043074              0.217666   
1                0.187099              0.001837              0.013031   
2                0.001385              0.142456              0.311013   
3                0.238346              0.052096             -0.061844   
4                0.589362              0.274844              0.192642   
..                    ...                   ...                   ...   
299              0.072100              0.123434              0.424522   
300              0.366695              0.178605              0.234547   
301              0.305006              0.315062             -0.056717   
302              0.147226              0.222755              0.396660   
303              0.046838             -0.043894              0.473756   

     184throw_19

In [176]:
model=LogisticRegression(random_state=42,class_weight={0: 1, 1: 10})

In [ ]:
from sklearn.model_selection import StratifiedKFold

# Define the number of splits
n_splits = 5

# Initialize StratifiedKFold
skf = StratifiedKFold(n_splits=n_splits, shuffle=True, random_state=42)
scores = []
roc_auc_scores = []
acc = []

# Define the threshold
threshold = 0.5

In [196]:
from lofo import LOFOImportance, Dataset, plot_importance

# Define thresholds
correlation_threshold = 0.6  # Adjust this value as needed

# Prepare the dataset for LOFO
dataset = Dataset(df=train, target=target, features=features,auto_group_threshold=correlation_threshold)

# Compute LOFO importance with correlation threshold
lofo = LOFOImportance(dataset, model=model, cv=skf,scoring='f1', n_jobs=-1)
importance_df = lofo.get_importance()
importance_df.to_csv('importance.csv', index=False)
# Filter features based on the importance threshold


Automatically grouped features by correlation:
1 ['SDQ_SDQ_Difficulties_Total', 'SDQ_SDQ_Externalizing', 'SDQ_SDQ_Generating_Impact', 'SDQ_SDQ_Hyperactivity']
2 ['0throw_10thcolumn', '10throw_100thcolumn']
3 ['0throw_119thcolumn', '0throw_17thcolumn']
4 ['0throw_21thcolumn', '6throw_21thcolumn']
5 ['0throw_134thcolumn', '0throw_165thcolumn', '0throw_58thcolumn']
6 ['0throw_87thcolumn', '87throw_100thcolumn', '88throw_100thcolumn']
7 ['0throw_106thcolumn', '100throw_106thcolumn', '100throw_109thcolumn', '8throw_100thcolumn']
8 ['0throw_118thcolumn', '105throw_117thcolumn', '105throw_118thcolumn']
9 ['0throw_137thcolumn', '100throw_137thcolumn']
10 ['0throw_166thcolumn', '102throw_166thcolumn', '104throw_166thcolumn', '105throw_166thcolumn', '2throw_166thcolumn', '60throw_104thcolumn']
11 ['0throw_179thcolumn', '100throw_179thcolumn']
12 ['1throw_107thcolumn', '1throw_9thcolumn']
13 ['1throw_118thcolumn', '1throw_16thcolumn']
14 ['1throw_20thcolumn', '20throw_103thcolumn']
15 ['1throw_12

100%|██████████| 1782/1782 [6:27:52<00:00, 13.06s/it]  


In [198]:
importance_df.sort_values(by='importance_mean', ascending=False, inplace=True)

In [202]:
# Extract filtered features from LOFO importance
filtered_features = importance_df[importance_df['importance_mean'] > 0]['feature'].tolist()

# Handle merged features by splitting them if necessary
processed_features = []
for feature in filtered_features:
    processed_features.extend(feature.split(' & '))  # Split and add individual features


# Remove duplicates and ensure proper formatting
processed_features = list(set(processed_features))

# Update train and test datasets with processed features
train = train[processed_features + ['participant_id', target]]
test = test[processed_features + ['participant_id']]

In [203]:
train

122throw_132thcolumn  16throw_54thcolumn  96throw_194thcolumn  \
0                -0.309503           -0.070032             0.807861   
1                -0.254138           -0.187956             0.796282   
2                -0.275681           -0.210036             0.813538   
3                -0.305400           -0.050705             0.791177   
4                -0.335570            0.144140             0.757324   
...                    ...                 ...                  ...   
1208             -0.012688            0.158655             0.873008   
1209              0.172900            0.230531             0.690179   
1210             -0.276356            0.128823             0.764352   
1211             -0.270565            0.030379             0.790487   
1212             -0.198514           -0.070840             0.796651   

      166throw_195thcolumn  62throw_69thcolumn  6throw_114thcolumn  \
0                 0.517123            0.162394           -0.340671   
1                -0.011399            0.248866           -0.110549   
2                 0.174381            0.449804           -0.199790   
3                 0.165549           -0.127514           -0.277969   
4                -0.177750            0.139887           -0.318080   
...                    ...                 ...                 ...   
1208              0.139420            0.156413           -0.060289   
1209              0.201130            0.287145            0.178999   
1210             -0.196919            0.600564            0.333800   
1211             -0.052367           -0.004617            0.125806   
1212              0.167039            0.498273           -0.094565   

      95throw_179thcolumn  96throw_186thcolumn  13throw_30thcolumn  \
0                0.470936             0.112515            0.171048   
1                0.106230             0.212144            0.005809   
2                0.524691             0.095206            0.150680   
3                0.366275             0.398137            0.012874   
4               -0.326149            -0.152996            0.050402   
...                   ...                  ...                 ...   
1208             0.452210             0.383234            0.502748   
1209             0.056451             0.265178            0.131851   
1210             0.204247             0.065307            0.247427   
1211             0.089262             0.208976            0.283394   
1212             0.198606             0.091753           -0.028962   

      101throw_106thcolumn  ...  88throw_112thcolumn  63throw_113thcolumn  \
0                -0.022592  ...            -0.145510             0.177953   
1                -0.027454  ...            -0.187710             0.244670   
2                 0.220315  ...            -0.048013            -0.178161   
3                 0.277329  ...             0.152947            -0.001532   
4                 0.071549  ...            -0.091367             0.287855   
...                    ...  ...                  ...                  ...   
1208              0.334511  ...            -0.458187             0.313216   
1209              0.182112  ...            -0.163674             0.081436   
1210              0.021661  ...            -0.043998             0.020479   
1211              0.448621  ...            -0.149270             0.124464   
1212             -0.115127  ...            -0.005237             0.170143   

      36throw_101thcolumn  6throw_59thcolumn  116throw_193thcolumn  \
0                0.226652          -0.165908             -0.013271   
1               -0.030194           0.152552             -0.234470   
2                0.206669           0.377564             -0.080728   
3               -0.186691           0.599149              0.065847   
4               -0.014701           0.010773              0.043515   
...                   ...                ...                   ...   
1208             0.500974          -0.050128            

In [204]:


for fold, (train_idx, val_idx) in enumerate(skf.split(train, train[target])):
    train_val = train.iloc[train_idx]
    test_val = train.iloc[val_idx]
    model.fit(train_val.drop(columns=['participant_id', target]), train_val[target])
    
    # Get probabilities and apply threshold
    probabilities = model.predict_proba(test_val.drop(columns=['participant_id', target]))[:, 1]
    predictions = (probabilities >= threshold).astype(int)
    
    print(predictions.sum() / len(predictions))
    scores.append(f1_score(test_val[target], predictions))
    roc_auc_scores.append(roc_auc_score(test_val[target], probabilities))
    acc.append(accuracy_score(test_val[target], predictions))


0.5925925925925926
0.5596707818930041
0.5679012345679012
0.5826446280991735
0.5785123966942148


In [205]:
scores,np.array(scores).mean()

([0.6017699115044248,
  0.5748987854251012,
  0.6486486486486487,
  0.6044444444444445,
  0.5982142857142857,
  0.5110132158590308,
  0.502283105022831,
  0.5765765765765766,
  0.5267857142857143,
  0.5739910313901345],
 np.float64(0.5718625718871192))

In [206]:
roc_auc_scores

[np.float64(0.7608433734939759),
 np.float64(0.705722891566265),
 np.float64(0.7919287211740043),
 np.float64(0.7175873304538911),
 np.float64(0.7675986966734865),
 np.float64(0.6097138554216868),
 np.float64(0.6420180722891565),
 np.float64(0.6860587002096435),
 np.float64(0.631128286731833),
 np.float64(0.6799272561945897)]

In [207]:
acc

[0.6296296296296297,
 0.5679012345679012,
 0.6790123456790124,
 0.6322314049586777,
 0.628099173553719,
 0.5432098765432098,
 0.551440329218107,
 0.6131687242798354,
 0.5619834710743802,
 0.6074380165289256]

In [208]:
sub = pd.read_csv('submission.csv')

In [209]:
test

122throw_132thcolumn  16throw_54thcolumn  96throw_194thcolumn  \
0                0.249297           -0.141182             0.833849   
1               -0.012391           -0.024732             0.809000   
2               -0.053640            0.197935             0.770740   
3               -0.186590            0.098589             0.802233   
4               -0.050516            0.038174             0.879194   
..                    ...                 ...                  ...   
299             -0.012093            0.064836             0.846704   
300             -0.201617            0.148120             0.811879   
301             -0.117026           -0.053063             0.881707   
302             -0.430433            0.375175             0.782758   
303             -0.088834            0.026559             0.753061   

     166throw_195thcolumn  62throw_69thcolumn  6throw_114thcolumn  \
0               -0.055159            0.223483           -0.232689   
1                0.128660            0.541222           -0.044023   
2               -0.211547            0.065440           -0.129514   
3               -0.042514            0.058376           -0.072157   
4                0.074071            0.127166           -0.078977   
..                    ...                 ...                 ...   
299             -0.060786            0.554993           -0.276566   
300              0.155165            0.308337            0.042421   
301              0.040022            0.267592           -0.250905   
302              0.296896            0.351259           -0.206794   
303             -0.131931            0.519319            0.169520   

     95throw_179thcolumn  96throw_186thcolumn  13throw_30thcolumn  \
0               0.332660             0.329149            0.080876   
1               0.034751             0.514835           -0.139913   
2               0.196300             0.301816            0.256537   
3               0.101775             0.276299            0.196438   
4               0.135323             0.330378            0.024604   
..                   ...                  ...                 ...   
299             0.415123             0.441192           -0.141825   
300            -0.074758             0.121626            0.513208   
301             0.040947             0.373158            0.297428   
302             0.329735             0.348150            0.077064   
303             0.254078             0.392471            0.113446   

     101throw_106thcolumn  ...  94throw_145thcolumn  88throw_112thcolumn  \
0                0.457548  ...             0.058295             0.128420   
1                0.289906  ...             0.135528            -0.401630   
2               -0.094878  ...            -0.126054             0.100088   
3               -0.146529  ...             0.113327            -0.129846   
4                0.279091  ...             0.026944             0.031887   
..                    ...  ...                  ...                  ...   
299             -0.199740  ...             0.249719             0.179497   
300             -0.041109  ...            -0.194993            -0.095892   
301              0.291660  ...             0.372888             0.128463   
302             -0.053262  ...             0.107508             0.088087   
303              0.221977  ...             0.450883            -0.075707   

     63throw_113thcolumn  36throw_101thcolumn  6throw_59thcolumn  \
0               0.465989             0.119470          -0.177713   
1               0.024253             0.100051           0.031289   
2              -0.042384             0.471909          -0.269533   
3               0.059607             0.220875           0.267186   
4               0.200477            -0.173628           0.009044   
..                   ...                  ...                ...   
299             0.113791            -0.129200           0.214203   
300             0.334209             0.361740    

In [210]:
train['adhd'] = adhd


/tmp/ipykernel_6003/3627532770.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train['adhd'] = adhd


In [211]:
test['adhd'] = sub['ADHD_Outcome']

/tmp/ipykernel_6003/3692363526.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test['adhd'] = sub['ADHD_Outcome']


In [212]:
features.append('adhd')

In [218]:
model.fit(train.drop(columns=['participant_id','Sex_F']),train['Sex_F'])

LogisticRegression(class_weight={0: 1, 1: 10}, random_state=42)

In [ ]:
probabilities = model.predict_proba(test.drop(columns='participant_id'))[:, 1]
sub['Sex_F'] = (probabilities >= threshold).astype(int)



In [221]:
sub['Sex_F'] = 1

In [222]:
sub.to_csv('submission.csv', index=False)


In [ ]:
np.array(scores).mean(),np.array(roc_auc_scores).mean(),np.array(acc).mean()

(np.float64(0.6055952151473809),
 np.float64(0.7487362026723245),
 np.float64(0.6273747576777879))